# StyleTTS-VC Demo


### Utils

In [1]:
%cd ..

/data/sky/StyleTTS-VC


In [2]:
# load packages
import random
import yaml
from munch import Munch
import numpy as np
import torch
from torch import nn
import torch.nn.functional as F
import torchaudio
import librosa

from models import *
from utils import *

%matplotlib inline

In [3]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [4]:
to_mel = torchaudio.transforms.MelSpectrogram(
    n_mels=80, n_fft=2048, win_length=1200, hop_length=300)
mean, std = -4, 4

def length_to_mask(lengths):
    mask = torch.arange(lengths.max()).unsqueeze(0).expand(lengths.shape[0], -1).type_as(lengths)
    mask = torch.gt(mask+1, lengths.unsqueeze(1))
    return mask

def preprocess(wave):
    wave_tensor = torch.from_numpy(wave).float()
    mel_tensor = to_mel(wave_tensor)
    mel_tensor = (torch.log(1e-5 + mel_tensor.unsqueeze(0)) - mean) / std
    return mel_tensor

def compute_style(ref_dicts):
    reference_embeddings = {}
    for key, path in ref_dicts.items():
        wave, sr = librosa.load(path, sr=24000)
        audio, index = librosa.effects.trim(wave, top_db=25)
        if sr != 24000:
            audio = librosa.resample(audio, sr, 24000)
        mel_tensor = preprocess(audio).to(device)

        with torch.no_grad():
            ref = model.style_encoder(mel_tensor.unsqueeze(1))
        reference_embeddings[key] = (ref.squeeze(1), audio)
    
    return reference_embeddings

### Load models

In [5]:
# load hifi-gan

import sys
sys.path.insert(0, "./Demo/hifi-gan")

import glob
import os
import argparse
import json
import torch
from scipy.io.wavfile import write
from attrdict import AttrDict
from vocoder import Generator
import librosa
import numpy as np
import torchaudio

h = None

def load_checkpoint(filepath, device):
    assert os.path.isfile(filepath)
    print("Loading '{}'".format(filepath))
    checkpoint_dict = torch.load(filepath, map_location=device)
    print("Complete.")
    return checkpoint_dict

def scan_checkpoint(cp_dir, prefix):
    pattern = os.path.join(cp_dir, prefix + '*')
    cp_list = glob.glob(pattern)
    if len(cp_list) == 0:
        return ''
    return sorted(cp_list)[-1]

cp_g = scan_checkpoint("Vocoder/LibriTTS/", 'g_')

config_file = os.path.join(os.path.split(cp_g)[0], 'config.json')
with open(config_file) as f:
    data = f.read()
json_config = json.loads(data)
h = AttrDict(json_config)

device = torch.device(device)
generator = Generator(h).to(device)

state_dict_g = load_checkpoint(cp_g, device)
generator.load_state_dict(state_dict_g['generator'])
generator.eval()
generator.remove_weight_norm()

Loading 'Vocoder/LibriTTS/g_00935000'
Complete.
Removing weight norm...


In [6]:
# simple fix for dataparallel that allows access to class attributes
class MyDataParallel(torch.nn.DataParallel):                
    def __getattr__(self, name):                            
        try: 
            return super().__getattr__(name)                
        except AttributeError:                              
            return getattr(self.module, name)   

In [7]:
# load StyleTTS
model_path = "./Models/VCTK/2/epoch_2nd_00004.pth"
model_config_path = "./Models/VCTK/config.yml"

config = yaml.safe_load(open(model_config_path))

# load pretrained ASR model
ASR_config = config.get('ASR_config', False)
ASR_path = config.get('ASR_path', False)
text_aligner = load_ASR_models(ASR_path, ASR_config)

# load pretrained F0 model
F0_path = config.get('F0_path', False)
pitch_extractor = load_F0_models(F0_path)

model = build_model(Munch(config['model_params']), text_aligner, pitch_extractor)

params = torch.load(model_path, map_location='cpu')
params = params['net']
for key in model:
    if key in params:
        if not "discriminator" in key:
            print('%s loaded' % key)
            model[key].load_state_dict(params[key])
_ = [model[key].eval() for key in model]
_ = [model[key].to(device) for key in model]

dict_keys(['net', 'val_loss', 'epoch'])
mel_encoder loaded
linear_proj loaded
decoder loaded
pitch_extractor loaded
text_encoder loaded
style_encoder loaded
text_aligner loaded


### Conversion (seen speakers)

In [8]:
# get first 3 validation sample as references

train_path = config.get('train_data', None)
val_path = config.get('val_data', None)
train_list, val_list = get_data_path_list(train_path, val_path)

t_list = []
with open("t.txt") as t:
    lines = t.readlines()
    for l in lines:
        t_list.append(l)
random.shuffle(t_list)

train_list = t_list[0:30000]
val_list = t_list[-111:]
    
ref_dicts = {}
for j in range(10):
    filename = val_list[j].split('|')[0]
    name = filename.split('/')[-1].replace('.wav', '')
    ref_dicts[name] = filename
    
reference_embeddings = compute_style(ref_dicts)

In [9]:
# get last validation sample as input 
# filename = val_list[-1].split('|')[0]
filename = "Demo/588.wav"
audio, source_sr = librosa.load(filename, sr=24000)
audio, index = librosa.effects.trim(audio, top_db=25)
audio = audio / np.max(np.abs(audio))
audio.dtype = np.float32
source = preprocess(audio).to(device)

In [10]:
converted_samples = {}

with torch.no_grad():
    mel_input_length = torch.LongTensor([source.shape[-1]])
    asr = model.mel_encoder(source)
    F0_real, _, F0 = model.pitch_extractor(source.unsqueeze(1))
    real_norm = log_norm(source.unsqueeze(1)).squeeze(1)
    
    for key, (ref, _) in reference_embeddings.items():
        out = model.decoder(asr, F0_real.unsqueeze(0), real_norm, ref.squeeze(1))

        c = out.squeeze()
        y_g_hat = generator(c.unsqueeze(0))
        y_out = y_g_hat.squeeze()

        converted_samples[key] = y_out.cpu().numpy()

In [11]:
import IPython.display as ipd
for key, wave in converted_samples.items():
    print('Converted: %s' % key)
    display(ipd.Audio(wave, rate=24000))
    try:
        print('Reference: %s' % key)
        display(ipd.Audio(reference_embeddings[key][-1], rate=24000))
    except:
        continue

print('Original:')
display(ipd.Audio(audio, rate=24000))

Converted: BAC009S0516W0476


Reference: BAC009S0516W0476


Converted: BAC009S0092W0349


Reference: BAC009S0092W0349


Converted: BAC009S0144W0311


...

Converted: BAC009S0112W0350


Reference: BAC009S0112W0350


Converted: BAC009S0078W0199


Reference: BAC009S0078W0199


Original:


### Conversion (unseen speakers)

In [12]:
# get first 3 test sample as references

test_path = val_path.replace('/val_list.txt', '/test_list.txt')
_, test_list = get_data_path_list(train_path, test_path)

test_list = t_list[50000:50100]

ref_dicts = {}
for j in range(3):
    filename = test_list[j].split('|')[0]
    name = filename.split('/')[-1].replace('.wav', '')
    ref_dicts[name] = filename

ref_dicts["2"] = "Demo/2.wav"
reference_embeddings = compute_style(ref_dicts)

In [13]:
# get last test sample as input 
# filename = test_list[-2].split('|')[0]
filename = "Demo/590.wav"
audio, source_sr = librosa.load(filename, sr=24000)
audio, index = librosa.effects.trim(audio, top_db=30)
audio = audio / np.max(np.abs(audio))
audio.dtype = np.float32
source = preprocess(audio).to(device)

In [14]:
converted_samples = {}

with torch.no_grad():
    mel_input_length = torch.LongTensor([source.shape[-1]])
    asr = model.mel_encoder(source)
    F0_real, _, F0 = model.pitch_extractor(source.unsqueeze(1))
    real_norm = log_norm(source.unsqueeze(1)).squeeze(1)
    
    for key, (ref, _) in reference_embeddings.items():
        out = model.decoder(asr, F0_real.unsqueeze(0), real_norm, ref.squeeze(1))

        c = out.squeeze()
        y_g_hat = generator(c.unsqueeze(0))
        y_out = y_g_hat.squeeze()

        converted_samples[key] = y_out.cpu().numpy()

In [15]:
import IPython.display as ipd
for key, wave in converted_samples.items():
    print('Converted: %s' % key)
    display(ipd.Audio(wave, rate=24000))
    try:
        print('Reference: %s' % key)
        display(ipd.Audio(reference_embeddings[key][-1], rate=24000))
    except:
        continue

print('Original:')
display(ipd.Audio(audio, rate=24000))

Converted: BAC009S0075W0176


Reference: BAC009S0075W0176


Converted: BAC009S0093W0150


Reference: BAC009S0093W0150


Converted: BAC009S0095W0249


Reference: BAC009S0095W0249


Converted: 2


Reference: 2


Original:
